In [0]:
from pyspark.sql.types import *
import pyspark
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
import pandas as pd
import json
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)

spark = SparkSession.builder.getOrCreate()

In [0]:
companies = spark.read.parquet('/dbfs/linkedin_train_data')
profiles=spark.read.parquet('/dbfs/linkedin_people_train_data')

In [0]:
profiles.schema

StructType([StructField('about', StringType(), True), StructField('avatar', StringType(), True), StructField('certifications', ArrayType(StructType([StructField('meta', StringType(), True), StructField('subtitle', StringType(), True), StructField('title', StringType(), True)]), True), True), StructField('city', StringType(), True), StructField('country_code', StringType(), True), StructField('current_company', StructType([StructField('company_id', StringType(), True), StructField('industry', StringType(), True), StructField('link', StringType(), True), StructField('name', StringType(), True), StructField('title', StringType(), True)]), True), StructField('current_company:company_id', StringType(), True), StructField('current_company:name', StringType(), True), StructField('education', ArrayType(StructType([StructField('degree', StringType(), True), StructField('end_year', StringType(), True), StructField('field', StringType(), True), StructField('meta', StringType(), True), StructField

In [0]:
skills = ['.net', '.netcore', '3d', 'ai', 'android', 'angular', 'aws', 
                   'python', 'javascript', 'react', 'machine learning', 'data science', 'react', 'angular', 'vue.js', 'node.js', 'express', 'django', 'flask', 'rails',
    'next.js', 'svelte', 'graphql', 'rest api', 'websockets', 'frontend', 'backend',
    'full stack', 'web development', 'tailwind', 'webpack', 'api',    'aws', 'azure', 'gcp', 'kubernetes', 'docker', 'terraform', 'serverless',
    'microservices', 'devops', 'ci/cd', 'cloud architecture', 'cloud computing',
    'distributed systems', 'system design', 'infrastructure', 'platform engineering','machine learning', 'deep learning', 'data science', 'neural networks',
    'tensorflow', 'pytorch', 'keras', 'nlp', 'computer vision', 'artificial intelligence',
    'data engineering', 'big data', 'data analytics', 'predictive analytics',
    'reinforcement learning', 'llm', 'generative ai', 'rag','sql', 'mongodb', 'postgresql', 'mysql', 'elasticsearch', 'redis', 'nosql',
    'data modeling', 'data warehousing', 'database design', 'data infrastructure','cybersecurity', 'security', 'penetration testing', 'ethical hacking',
    'infosec', 'network security', 'cloud security', 'cryptography',
    'security engineering', 'application security', 'devsecops','blockchain', 'web3', 'artificial intelligence', 'virtual reality',
    'augmented reality', 'quantum computing', 'iot', 'crypto', 'nft',
    'spatial computing', 'robotics','software architecture', 'clean code', 'test driven development',
    'agile development', 'software engineering', 'system design',
    'design patterns', 'code review', 'software testing', 'domain driven design',
    'microservices', 'scalable systems','ios', 'android', 'react native', 'flutter', 'mobile development',
    'swift', 'kotlin', 'mobile apps', 'app development','unity', 'unreal engine', 'game development', 'gameplay programming',
    '3d', 'computer graphics'
]

In [0]:
# התקנה מחדש של PyTorch
%pip install --upgrade torch torchvision torchaudio sentence-transformers


  Obtaining dependency information for torch from https://files.pythonhosted.org/packages/78/a9/97cbbc97002fff0de394a2da2cdfa859481fdca36996d7bd845d50aa9d8d/torch-2.6.0-cp311-cp311-manylinux1_x86_64.whl.metadata
  Obtaining dependency information for torchvision from https://files.pythonhosted.org/packages/be/a2/b0cedf0a411f1a5d75cfc0b87cde56dd1ddc1878be46a42c905cd8580220/torchvision-0.21.0-cp311-cp311-manylinux1_x86_64.whl.metadata
  Obtaining dependency information for torchaudio from https://files.pythonhosted.org/packages/3e/00/2c69d436c613043f3051210d2f84a4c9062a815fa609c5f54d25ea8bfd07/torchaudio-2.6.0-cp311-cp311-manylinux1_x86_64.whl.metadata
  Obtaining dependency information for sentence-transformers from https://files.pythonhosted.org/packages/05/89/7eb147a37b7f31d3c815543df539d8b8d0425e93296c875cc87719d65232/sentence_transformers-3.4.1-py3-none-any.whl.metadata
  Obtaining dependency information for nvidia-cuda-nvrtc-cu12==12.4.127 from https://files.pythonhosted.org/packag

In [0]:
%pip install --upgrade pip
%pip install --upgrade torch torchvision torchaudio sentence-transformers


  Obtaining dependency information for pip from https://files.pythonhosted.org/packages/85/8a/1ddf40be20103bcc605db840e9ade09c8e8c9f920a03e9cfe88eae97a058/pip-25.0-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/1.8 MB ? eta -:--:--
   ━━━━━━╸━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.3/1.8 MB 9.3 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 32.5 MB/s eta 0:00:00
  Attempting uninstall: pip
    Found existing installation: pip 23.2.1
    Uninstalling pip-23.2.1:
      Successfully uninstalled pip-23.2.1
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
##Finding the intial high-tech people -set

In [0]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd

# Initialize the model
model = SentenceTransformer('all-MiniLM-L6-v2')

# Function to generate embeddings for different column combinations
def generate_embeddings(profiles_df, fields):
    profile_texts = []
    
    for _, row in profiles_df.iterrows():
        profile_text = ""
        
        # Core fields
        if 'position' in fields:
            profile_text += f"Position: {row.get('position', '')} \n"
        if 'about' in fields:
            profile_text += f"About: {row.get('about', '')} \n"
        if 'current_company' in fields:
            current_company = row.get('current_company', {}) or {}
            company_title = current_company.get('title', '') if isinstance(current_company, dict) else ''
            profile_text += f"Current Company: {company_title} \n"

        # Experience
        if 'experience' in fields and isinstance(row.get('experience'), list):
            experiences = []
            for exp in row['experience']:
                if isinstance(exp, dict):
                    exp_text = f"{exp.get('title', '')} {exp.get('description', '')}"
                    experiences.append(exp_text)
            profile_text += f"Experience: {' '.join(experiences)} \n"

        # Education
        if 'education' in fields and isinstance(row.get('education'), list):
            education = []
            for edu in row['education']:
                if isinstance(edu, dict):
                    edu_text = f"{edu.get('degree', '')} {edu.get('field', '')}"
                    education.append(edu_text)
            profile_text += f"Education: {' '.join(education)} \n"

        # Certifications
        if 'certifications' in fields and isinstance(row.get('certifications'), list):
            certifications = [cert.get('title', '') for cert in row['certifications'] if isinstance(cert, dict)]
            profile_text += f"Certifications: {', '.join(certifications)} \n"

        # Languages
        if 'languages' in fields and isinstance(row.get('languages'), list):
            languages = [lang.get('title', '') for lang in row['languages'] if isinstance(lang, dict)]
            profile_text += f"Languages: {', '.join(languages)} \n"

        # Volunteer Experience
        if 'volunteer_experience' in fields and isinstance(row.get('volunteer_experience'), list):
            volunteer_experiences = []
            for vol in row['volunteer_experience']:
                if isinstance(vol, dict):
                    vol_text = f"{vol.get('title', '')} {vol.get('cause', '')}"
                    volunteer_experiences.append(vol_text)
            profile_text += f"Volunteer Experience: {' '.join(volunteer_experiences)} \n"

        profile_texts.append(profile_text.strip())
    
    return model.encode(profile_texts)

# Example usage:
fields_variants = [
    ['position', 'about', 'current_company'],  # Core fields
    ['position', 'about', 'current_company', 'experience'],  # Core + Experience
    ['position', 'about', 'current_company', 'education'],  # Core + Education
    ['position', 'about', 'current_company', 'certifications', 'languages'],  # Core + Certifications + Languages
    ['position', 'about', 'current_company', 'volunteer_experience', 'experience']  # Core + Volunteer + Experience
]

# Limit the sample size to 1,0000 rows
profiles_df = (profiles.filter(profiles.id.isNotNull() & 
                             profiles.about.isNotNull() & 
                             profiles.position.isNotNull())
              .select('id', 'position', 'about', 'current_company', 
                     'experience', 'certifications', 'education')
              .limit(300000)
              .toPandas())

# Iterate through combinations and calculate embeddings
all_results = {}
tech_context = "Technology professional with expertise in: " + ", ".join(skills)
tech_embedding = model.encode([tech_context])[0]

for fields in fields_variants:
    profile_embeddings = generate_embeddings(profiles_df, fields)
    similarities = cosine_similarity([tech_embedding], profile_embeddings)[0]

    # Analyze results for this combination
    threshold = 0.45
    tech_matches = []
    for idx, score in enumerate(similarities):
        if score > threshold:
            profile = profiles_df.iloc[idx]
            current_company = profile.get('current_company', {}) or {}
            company_title = current_company.get('title', '') if isinstance(current_company, dict) else ''
            tech_matches.append({
                'id': profile.get('id', ''),
                'position': profile.get('position', ''),
                'similarity_score': float(score),
                'current_company': company_title,
                'about': profile.get('about', '')[:200] + '...' if profile.get('about') else ''
            })

    results_df = pd.DataFrame(tech_matches)
    results_df.sort_values('similarity_score', ascending=False, inplace=True)

    # Save results for this combination
    combination_name = "_".join(fields)
    results_df.to_csv(f'tech_profiles_results_all_{combination_name}.csv', index=False)

    # Print details about the results
    print(f"Combination: {combination_name}")
    print(f"Total profiles: {len(profiles_df)}")
    print(f"Profiles above threshold ({threshold}): {len(results_df)}")
    for acc_threshold in [0.4, 0.5, 0.6, 0.7, 0.8]:
        acc_count = len(results_df[results_df['similarity_score'] > acc_threshold])
        print(f"Profiles > {acc_threshold}: {acc_count}")
    print("\n")

    all_results[tuple(fields)] = results_df

# Save summary of all combinations
print("Analysis complete. Results saved for all combinations.")

/databricks/python/lib/python3.11/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Combination: position_about_current_company
Total profiles: 300000
Profiles above threshold (0.45): 4264
Profiles > 0.4: 4264
Profiles > 0.5: 1738
Profiles > 0.6: 185
Profiles > 0.7: 7
Profiles > 0.8: 0


Combination: position_about_current_company_experience
Total profiles: 300000
Profiles above threshold (0.45): 4264
Profiles > 0.4: 4264
Profiles > 0.5: 1738
Profiles > 0.6: 185
Profiles > 0.7: 7
Profiles > 0.8: 0




com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$5(SequenceExecutionState.scala:136)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:136)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3$adapted(SequenceExecutionState.scala:133)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:133)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:728)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:446)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:446)
	at com.databricks.spark.chauffeur.ExecutionContextManagerV1.can

###Expanding the high-tech people based on similarity

In [0]:
!pip install fastparquet


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/1.8 MB ? eta -:--:--
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 62.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 0.0/2.4 MB ? eta -:--:--
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 72.8 MB/s eta 0:00:00
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import pandas as pd
from pyspark.sql import SparkSession

# Initialize Spark session

# Load profiles as a Spark DataFrame
profiles_spark_df = profiles.limit(300000)  # Assuming `profiles` is already a Spark DataFrame

# Load the high-tech group results (as a Pandas DataFrame)
results_df = pd.read_csv("/Workspace/Users/soaadhamood@campus.technion.ac.il/DataSets/tech_profiles_results_all_position_about_current_company_experience.csv")

# Function to generate embeddings for the specified fields
def generate_embeddings(df, fields):
    """
    Placeholder function to generate embeddings.
    Replace this with your actual logic for generating embeddings.
    """
    embeddings = np.random.rand(len(df), 128)  # Example: 128-dimensional random embeddings
    return embeddings

# Step 1: Process the Spark DataFrame in chunks and convert to Pandas
chunk_size = 100000  # Define chunk size based on memory capacity
profiles_pd_list = []
offset = 0

# Using Spark's `.toPandas()` directly on large data can cause memory overflow.
# Instead, iterate over partitions efficiently.
total_count = profiles_spark_df.count()

while offset < total_count:
    chunk = profiles_spark_df.limit(chunk_size).toPandas()
    profiles_pd_list.append(chunk)
    offset += chunk_size

# Step 2: Generate embeddings for profiles in chunks
all_embeddings_list = []
for profiles_pd_chunk in profiles_pd_list:
    embeddings_chunk = generate_embeddings(
        profiles_pd_chunk,
        fields=['position', 'about', 'current_company', 'experience', 'education']
    )
    all_embeddings_list.append(embeddings_chunk)

# Combine embeddings for all profiles
all_embeddings = np.vstack(all_embeddings_list)

# Step 3: Generate embeddings for high-tech group
high_tech_profiles = profiles_pd_list[0][profiles_pd_list[0]['id'].isin(results_df['id'])]
high_tech_embeddings = generate_embeddings(
    high_tech_profiles,
    fields=['position', 'about', 'current_company', 'experience', 'education']
)

# Step 4: Compute similarity using optimized chunk-wise processing
similarity_matrix = cosine_similarity(high_tech_embeddings, all_embeddings)

# Step 5: Find the maximum similarity score for each profile efficiently
max_similarities = np.max(similarity_matrix, axis=0)
for profiles_pd_chunk in profiles_pd_list:
    profiles_pd_chunk['max_similarity'] = max_similarities[:len(profiles_pd_chunk)]
    max_similarities = max_similarities[len(profiles_pd_chunk):]

# Step 6: Define a threshold for expanding the high-tech group
threshold = 0.4
expanded_high_tech_list = []
for profiles_pd_chunk in profiles_pd_list:
    expanded_chunk = profiles_pd_chunk[profiles_pd_chunk['max_similarity'] >= threshold]
    expanded_high_tech_list.append(expanded_chunk)

# Combine all expanded chunks into one DataFrame
expanded_high_tech = pd.concat(expanded_high_tech_list, ignore_index=True)

# Save the original and expanded high-tech groups to CSV files
high_tech_profiles.to_csv("original_high_tech_profiles.csv", index=False)
expanded_high_tech.to_csv("expanded_high_tech_profiles.csv", index=False, compression='gzip')


# Print statistics about the groups
print(f"Original high-tech group size: {len(high_tech_profiles)}")
print(f"Expanded high-tech group size: {len(expanded_high_tech)}")

# Print statistics for various similarity thresholds
for acc_threshold in [0.4, 0.5, 0.6, 0.7, 0.8]:
    count = len(expanded_high_tech[expanded_high_tech['max_similarity'] >= acc_threshold])
    print(f"Profiles with max_similarity >= {acc_threshold}: {count}")


Original high-tech group size: 262
Expanded high-tech group size: 300000
Profiles with max_similarity >= 0.4: 300000
Profiles with max_similarity >= 0.5: 300000
Profiles with max_similarity >= 0.6: 300000
Profiles with max_similarity >= 0.7: 300000
Profiles with max_similarity >= 0.8: 277779


##Classifying the high-tech people into mentors and mentees

In [0]:
import pandas as pd
import re
from datetime import date
from dateutil import parser
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, expr, lit, when, avg
from pyspark.sql.types import DoubleType
from pyspark.sql import functions as F

In [0]:
# Step 1: Load the Compressed Data
file_path = "/Workspace/Users/soaadhamood@campus.technion.ac.il/expanded_high_tech_profiles.csv"  # Update with your file path
expanded_high_tech_df = pd.read_csv(file_path, compression='gzip')

/root/.ipykernel/1808/command-2352773491670508-2481356206:3: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  expanded_high_tech_df = pd.read_csv(file_path, compression='gzip')


In [0]:
# Step 2: Display the Data
print("First few rows of the expanded dataset:")
print(expanded_high_tech_df.head())

First few rows of the expanded dataset:
  about  ... max_similarity
0   NaN  ...       0.816299
1   NaN  ...       0.817411
2   NaN  ...       0.821410
3   NaN  ...       0.805306
4   NaN  ...       0.796755

[5 rows x 27 columns]


In [0]:
# Step 3: Apply Classification Logic

# Convert the Pandas DataFrame to a Spark DataFrame
df = spark.createDataFrame(expanded_high_tech_df)

In [0]:
# Add a column for the number of degrees
df_with_num_degrees = df.withColumn("num_degrees", expr("size(split(education, ','))").cast("int"))


In [0]:
# Function to parse duration strings
def parse_duration(duration_str):
    if not duration_str:
        return 0.0
    years = 0
    months = 0
    match_years = re.search(r'(\d+)\s+year', duration_str.lower())
    if match_years:
        years = int(match_years.group(1))
    match_months = re.search(r'(\d+)\s+month', duration_str.lower())
    if match_months:
        months = int(match_months.group(1))
    return years * 12.0 + months

# Function to parse date strings
def parse_date_str(dt_str):
    if not dt_str:
        return None
    dt_str_lower = dt_str.strip().lower()
    if dt_str_lower == "present":
        return date.today()
    try:
        return parser.parse(dt_str).date()
    except Exception:
        return None

# Function to compute total experience in months
def total_experience(experience_array):
    total_months = 0.0
    if experience_array:
        for exp in experience_array:
            if exp and "duration" in exp and exp["duration"]:
                total_months += parse_duration(exp["duration"])
            elif exp and "duration_short" in exp and exp["duration_short"]:
                total_months += parse_duration(exp["duration_short"])
            elif exp and "positions" in exp and exp["positions"]:
                for pos in exp["positions"]:
                    if pos and "duration" in pos and pos["duration"]:
                        total_months += parse_duration(pos["duration"])
                    elif pos and "duration_short" in pos and pos["duration_short"]:
                        total_months += parse_duration(pos["duration_short"])
    return total_months

In [0]:
# Register the UDF
total_experience_udf = F.udf(total_experience, DoubleType())

# Add a column for total experience in years
final_df = df_with_num_degrees.withColumn(
    "total_experience_years",
    total_experience_udf("experience") / 12.0  # Convert months to years
)

In [0]:
# Define point values
num_degrees_points = 5
exp_years_points = 7

# Calculate total points
final_df = final_df.withColumn(
    "total_points",
    col("num_degrees") * num_degrees_points + col("total_experience_years") * exp_years_points,
)

In [0]:
# Classification Based on a Threshold
THRESHOLD = 50
final_df = final_df.withColumn(
    "is_above_threshold",
    when(col("total_points") > THRESHOLD, lit(1)).otherwise(lit(0))
)

# Classification Based on Average
avg_value = final_df.select(avg(col("total_points"))).collect()[0][0]
final_df = final_df.withColumn(
    "is_above_avg",
    when(col("total_points") > avg_value, lit(1)).otherwise(lit(0))
)

# Display the final DataFrame
final_df.show()

+-----+--------------------+--------------------+--------------------+------------+--------------------+--------------------------+--------------------+--------------------+--------------------+--------------------+---------+---------+------+--------------------+--------------------+--------------------+--------------------+--------------------+-----+---------------+---------------------+----------+--------------------+--------------------+--------------------+------------------+-----------+----------------------+------------+------------------+------------+
|about|              avatar|      certifications|                city|country_code|     current_company|current_company:company_id|current_company:name|           education|  educations_details|          experience|followers|following|groups|                  id|           languages|                name|  people_also_viewed|            position|posts|recommendations|recommendations_count| timestamp|                 url|volunteer_ex

In [0]:

display(final_df)


about avatar certifications city country_code current_company current_company:company_id current_company:name education educations_details experience followers following groups id languages name people_also_viewed position posts recommendations recommendations_count timestamp url volunteer_experience сourses max_similarity num_degrees total_experience_years total_points is_above_threshold is_above_avg null https://media.licdn.com/dms/image/C4D03AQE-B0QzjS1Cgw/profile-displayphoto-shrink_800_800/0/1517524530883?e=2147483647&v=beta&t=xKHfKdT1DZxpZWl18-G7N7gjacJaqkxBJ6v-JzxXXEo [] Holland, Michigan, United States US {'company_id': None, 'industry': 'Michigan Conference of the United Methodist Church', 'link': None, 'name': 'Michigan Conference of the United Methodist Church', 'title': 'retired at Michigan Conference of the United Methodist Church'} null Michigan Conference of the United Methodist Church [] null [{'company': None, 'company_id': None, 'description': None, 'duration': 'Jun 1992 - Present 31 years 4 months', 'duration_short': '31 years 4 months', 'end_date': 'Present', 'location': None, 'positions': None, 'start_date': 'Jun 1992', 'subtitle': 'Michigan Conference of the United Methodist Church', 'subtitleURL': None, 'title': 'retired', 'url': None}] 76 76 [] glenn-wagner-366824138 [] Glenn Wagner [{'profile_link': 'https://www.linkedin.com/in/gerald-allison-b9b78080?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/mzammit08?trk=public_profile_browsemap'}
 {'profile_link': 'https://au.linkedin.com/in/mikezammitmelbaus?trk=public_profile_browsemap'}
 {'profile_link': 'https://au.linkedin.com/in/mike-zammit-cima%C2%AE-07a1123a?trk=public_profile_browsemap'}
 {'profile_link': 'https://ca.linkedin.com/in/michael-zammit-573b2261?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/phil-jones-29018a13?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/al-trucano-27954955?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/sharon-cress-b0814690?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/ron-bentzinger-327a35177?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/eloise-saltzgaver-48a08668?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/george-klohck-33b38597?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/dennis-shaw-92087017?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/james-kayler-bb9556a1?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/sue-ann-salmon-60a16433?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/gordon-packard-6777a591?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/loy-lilley-90b27758?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/john-mcfarlane-2a8376114?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/duane-mevis-b66a6128?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/george-white-054a6b42?trk=public_profile_browsemap'}
 {'profile_link': 'https://www.linkedin.com/in/jane-wood-37a18a79?trk=public_profile_browsemap'}] retired at Michigan Conference of the United Methodist Church [] [] null 2023-09-04 https://www.linkedin.com/in/glenn-wagner-366824138 [] [] 0.8162991428610017 1 0.0 5.0 0 0 null https://media.licdn.com/dms/image/C4D03AQE-F_SOngHmkA/profile-displayphoto-shrink_800_800/0/1618610169232?e=2147483647&v=beta&t=Xg7mvCdrJbKYJS51k8xxUHXINN4WitaI6kAh1-SqlN8 [] Topeka, Kansas, United States US {'company_id': 'bcbsks', 'industry': 'Blue Cross and Blue Shield of Kansas', 'link': 'https://my.linkedin.com/company/bcbsks?trk=public_profile_topcard-current-company', 'name': 'Blue Cross and Blue Shield of Kansas', 'title': 'IT Infrastructure Administrator'} bcbsks Blue Cross and 

In [0]:
from pyspark.sql.functions import col

# Filter mentors: individuals who crossed the threshold
mentors_df = final_df.filter(col("is_above_threshold") == 1)

# Filter mentees: individuals who did not cross the threshold
mentees_df = final_df.filter(col("is_above_threshold") == 0)

# Display the first few rows of each DataFrame
print("Mentors:")
mentors_df.show()

print("Mentees:")
mentees_df.show()


Mentors:
+-----+--------------------+--------------------+--------------------+------------+--------------------+--------------------------+--------------------+--------------------+--------------------+--------------------+---------+---------+------+--------------------+--------------------+----------------+--------------------+--------------------+-----+--------------------+---------------------+----------+--------------------+--------------------+-------+------------------+-----------+----------------------+------------+------------------+------------+
|about|              avatar|      certifications|                city|country_code|     current_company|current_company:company_id|current_company:name|           education|  educations_details|          experience|followers|following|groups|                  id|           languages|            name|  people_also_viewed|            position|posts|     recommendations|recommendations_count| timestamp|                 url|volunteer_expe

In [0]:
pip install sentence-transformers


Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
from sentence_transformers import SentenceTransformer
from pyspark.sql.functions import pandas_udf, PandasUDFType
from pyspark.sql.types import ArrayType, FloatType
import pandas as pd


2025-02-07 11:40:22.228586: I external/local_tsl/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-02-07 11:40:22.428685: I external/local_tsl/tsl/cuda/cudart_stub.cc:32] Could not find cuda drivers on your machine, GPU will not be used.
2025-02-07 11:40:23.368701: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-02-07 11:40:30.487176: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [0]:
model = SentenceTransformer('all-MiniLM-L6-v2')


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

/databricks/python/lib/python3.11/site-packages/huggingface_hub/file_download.py:795: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


...

tokenizer_config.json:   0%|          | 0.00/350 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [0]:
@pandas_udf(ArrayType(FloatType()), functionType=PandasUDFType.SCALAR)
def compute_embeddings(text_series: pd.Series) -> pd.Series:
    embeddings = model.encode(text_series.tolist(), convert_to_numpy=True)
    return pd.Series([embedding.tolist() for embedding in embeddings])


/databricks/spark/python/pyspark/sql/pandas/functions.py:441: UserWarning: In Python 3.6+ and Spark 3.0+, it is preferred to specify type hints for pandas UDF instead of specifying pandas UDF type which will be deprecated in the future releases. See SPARK-28264 for more details.
  warnings.warn(


In [0]:
from pyspark.sql.functions import concat_ws, col

# Define the columns to concatenate
columns_to_concatenate = ['position', 'about', 'current_company', 'experience', 'education']

# Concatenate columns into a single 'combined_text' column, using a space as a separator
mentors_df = mentors_df.withColumn('combined_text', concat_ws(' ', *[col(c) for c in columns_to_concatenate]))


In [0]:
mentors_with_embeddings_df = mentors_df.withColumn('embeddings', compute_embeddings(mentors_df['combined_text']))


In [0]:
mentors_with_embeddings_df.select('combined_text', 'embeddings').show(truncate=False)


+---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------